In [1]:
import random
import string
import torch
import wandb
import itertools
import argparse


import numpy as np
import pandas as pd

from torch.utils import data
from torch.utils.data import DataLoader
from tqdm import tqdm

from Code import Dataloader
from Code import Dataset
from Code import ModelBertV1
from Code import Train

from sklearn.model_selection import train_test_split

import Code.ModelBertV1 as ModelLib

import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from tqdm import tqdm
import datetime


In [2]:

def load_model(path, map_location='cuda'):
    checkpoint = torch.load(path, map_location=map_location, weights_only=False)
    config = checkpoint.get('config', None)
    # config['df_config'].address_limit = config['cnt_known_address']
    model = getattr(ModelBertV1, config['model'])(
                known_address_len=config['cnt_known_address'],
                **config['model_params']
            )

    model.load_state_dict(checkpoint['model_state_dict'])
    epoch = checkpoint.get('epoch', None)

    return model, config, epoch

def get_ts(data):
    return (data.loc[:, 'timestamp'].values.astype('datetime64[ns]') -  np.datetime64('1970-01-01T00:00:00')) \
            / np.timedelta64(1, 'ns')

In [36]:
class TimeEmbeddingRegressionDataset(data.Dataset):
    def __init__(self, df, model, sample_len, apply_log=False,
                 device='cpu', batch_size=128, cnt_batchs=-1,
                 target_type: str="timestamp", target_transform_params={}):
        self.model = model.eval().to(device)
        self.df = df.reset_index(drop=True)
        self.sample_len = sample_len
        self.apply_log = apply_log
        self.device = device
        self.batch_size = batch_size
        self.target_name = target_type
        self.target_transform_params = target_transform_params

        if cnt_batchs == -1:
            cnt_batchs = len(df) // (self.batch_size * self.sample_len) + 1
        self.cnt_batchs = cnt_batchs

        self.samples = self.build_samples(df)
        self.embeddings, self.targets = self.compute_all_embeddings()

    def build_samples(self, df):
        return list(range(
            min(len(df), self.batch_size * self.sample_len * self.cnt_batchs) // self.sample_len * self.sample_len))

    def __len__(self):
        return len(self.samples)

    def compute_target(self, idx: int) -> float:
        if self.target_name == "timestamp":
            return self.df.iloc[idx]["timestamp"]

        if self.target_name == "1h_volume":
            return self.df.iloc[idx]["1h_volume"]
        else:
            raise ValueError(f"Unsupported target: {self.target_name}")

    def get_target_transform(self, target):
        if self.target_name == "timestamp":
            mean = self.target_transform_params['mean']
            std = self.target_transform_params['std']

            return (target - mean) / std
        else:
            raise ValueError(f"Unsupported target: {self.target_name}")
        
    def revers_target_transfrom(self, pred):
        if self.target_name == "timestamp":
            mean = self.target_transform_params['mean']
            std = self.target_transform_params['std']
            return pred * std + mean
        else:
            raise ValueError(f"Unsupported target: {self.target_name}")

    def compute_all_embeddings(self):
        all_embs, all_tgts = [], []
        loader = DataLoader(self.samples[::self.sample_len], batch_size=self.batch_size, shuffle=False)

        for batch_indices in tqdm(itertools.islice(loader, self.cnt_batchs), desc="Embedding calculation", total=
                                  min(self.cnt_batchs, len(loader))):
            batch = [self._prepare_sample(int(idx)) for idx in batch_indices]

            smaples = self._collate_inputs([b[0] for b in batch])
            targets = torch.stack([b[1] for b in batch]).to(self.device)

            msk_ind, change_ind, save_ind, model_inputs = Train.batch_to_model(
                smaples,
                p_msk=0.0,
                p_change=0.0,
                p_save=1.0,
                device=self.device,
                change_strategy=Train.uniform_change_strategy
            )

            # for k, v in model_inputs.items():
            #     print(f"{k}: {v.shape}")
            #     print(v.device)

            with torch.no_grad():
                result = self.model(**model_inputs)['result']

            all_embs.append(result.cpu())
            all_tgts.append(targets.cpu())

        print(torch.cat(all_embs, 0).shape)
        return torch.cat(all_embs, 0).reshape(-1, all_embs[0].shape[-1]), torch.cat(all_tgts, 0).reshape(-1, 1)

    def _prepare_sample(self, idx):
        i = idx
        batch_df = self.df.iloc[i:i + self.sample_len]
        ts = get_ts(batch_df)
        time_features = Dataset.extract_time_features(ts)
        from_ind = batch_df['from'].values
        to_ind = batch_df['to'].values
        values = batch_df['value'].values

        volume_converter = lambda x: x
        if self.apply_log:
            volume_converter = lambda x: np.log(x)

        sample = {
            'numeric_features': torch.tensor(values, dtype=torch.float).T.unsqueeze(0).unsqueeze(-1),
            'from_address': torch.tensor(from_ind, dtype=torch.long).T.unsqueeze(0),
            'to_address': torch.tensor(to_ind, dtype=torch.long).T.unsqueeze(0),
            'time_features': torch.tensor(time_features, dtype=torch.float).T.unsqueeze(0),
            'value': torch.tensor(volume_converter(values)).unsqueeze(0).unsqueeze(-1)
        }

        target = torch.tensor([self.compute_target(k) for k in range(i, i + self.sample_len)], dtype=torch.float)
        return sample, target

    def _collate_inputs(self, input_list):
        batched = {}
        for key in input_list[0].keys():
            batched[key] = torch.cat([torch.tensor(item[key]) for item in input_list], dim=0)
        return batched

    def __getitem__(self, idx):
        return self.embeddings[idx], self.targets[idx]


In [124]:
class SimpleRegressor(nn.Module):
    def __init__(self, hidden_dim):
        super().__init__()
        self.net = nn.Sequential(
            nn.LazyLinear(hidden_dim),
            nn.SiLU(),
            nn.LazyLinear(hidden_dim),
            nn.SiLU(),
            nn.LazyLinear(hidden_dim),
            nn.SiLU(),
            nn.LazyLinear(1)
        )

    def forward(self, x):
        return self.net(x)


class TargetLogger:
    def __init__(self, target_type: str, run_name):
        self.target_type = target_type
        self.run_id = ''.join(random.choice(string.ascii_lowercase) for _ in range(5))
        self.run = wandb.init(name=f'{run_name} {self.run_id} {self.target_type}')

    def log(self, train_loss: float, val_loss: float, lr: float, epoch: int):
        log_data = {
            "train_loss": train_loss,
            "val_loss": val_loss,
            "lr": lr,
            "epoch": epoch,
        }

        # if self.target_type == "timestamp":
        #     log_data["val_timedelta"] = datetime.timedelta(seconds=val_loss)

        wandb.log(log_data)

    def finish(self):
        self.run.finish()

In [28]:
def train_time_regressor(model, train_dataloader, val_dataloader, num_epochs=100,
                         lr=10, device='cuda', std=1, mean=0, normilize=True, logger: TargetLogger | None = None):
    std = float(std)
    mean = float(mean)
    model = model.to(device)
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
    criterion = nn.MSELoss()
    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
        optimizer,
        mode='min',
        factor=0.7,
        patience=7,
        min_lr=1e-6,
        threshold=0.01,
    )

    for epoch in range(num_epochs):
        model.train()
        total_train_loss = 0.0
        for emb_time, target in tqdm(train_dataloader, desc=f"Epoch {epoch + 1} - Train"):
            if normilize:
                emb_time = emb_time / emb_time.norm(2, 1, keepdim=True)
            emb_time = emb_time.to(device)
            target = (target.to(device).unsqueeze(-1).float() - mean) / std

            pred = model(emb_time)
            loss = criterion(pred, target)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            total_train_loss += loss.item()

        model.eval()
        total_val_loss = 0.0
        with torch.no_grad():
            for emb_time, target in tqdm(val_dataloader, desc=f"Epoch {epoch + 1} - Val"):
                if normilize:
                    emb_time = emb_time / emb_time.norm(2, 1, keepdim=True)
                emb_time = emb_time.to(device)
                target = (target.to(device).unsqueeze(-1).float() - mean) / std

                pred = model(emb_time)
                loss = criterion(pred, target)
                total_val_loss += loss.item()

        avg_val_loss = (total_val_loss / len(val_dataloader)) ** 0.5 * std
        scheduler.step(avg_val_loss)

        print(f"Epoch {epoch + 1}")
        print(f"\nLr: {optimizer.param_groups[0]['lr']}")
        avg_train_loss = (total_train_loss / len(train_dataloader)) ** 0.5 * std
        print(f"\nTrain Loss: {avg_train_loss:.4f}")
        print(f"\nVal Loss: {avg_val_loss:.4f}")
        print(f"\nTimedelta: {datetime.timedelta(seconds=avg_val_loss)}")

        lr = optimizer.param_groups[0]['lr']
        logger.log(avg_train_loss, avg_val_loss, lr, epoch)



In [29]:
device = 'cuda:6' # args.device
target_type = '1h_volume'
batch_size = 2**14
lr = 0.5
hidden_dim = 32
model_epochs = 1951
study_epoch = 100
run_name = 'test script'
run_hash =  'gtczylpkfb'

path = ('/home/motatasher/Documents/University/Diploma/'
            'Diploma/models/')
import os

for run in os.listdir(path):
    folder_path = os.path.join(path, run)
    if folder_path[-2:] != 'pt' and run.split('_')[-1] == run_hash:
        epochs = {int(x.replace('.', '_').split('_')[-2]): x for x in os.listdir(folder_path)}
        config_path = os.path.join(folder_path, epochs.get(model_epochs, max(epochs.keys())))

print(config_path)
model, config, epoch = load_model(config_path)



/home/motatasher/Documents/University/Diploma/Diploma/models/model training on eth dataset v1, tensor predict, small bert_gtczylpkfb/model_epoch_1951.pt
Params in model: 316704


In [8]:
df_raw = getattr(Dataloader, config['dataset_fabric'])(**config['df_config'], address_limit=config['cnt_known_address'])

ts = df_raw["timestamp"].values
values = df_raw["value"].values
df_size = len(df_raw)
prefix_sum = np.zeros(df_size + 1)
prefix_sum[1:] = np.cumsum(values)
future_volume = np.zeros(df_size)
j = 0
for i in tqdm(range(df_size)):
    while j < df_size and ts[j] <= ts[i] + 3600:
        j += 1
    future_volume[i] = prefix_sum[j] - prefix_sum[i + 1]
df_raw["1h_volume"] = np.log(future_volume)

df_raw = df_raw[future_volume > 0]

train_data, val_data = train_test_split(df_raw, test_size=1/4, shuffle=False)
print(f"square std of all: {df_raw['value'].std() ** 2}\nTrain: {train_data['value'].std() ** 2}\nVal: {val_data['value'].std() ** 2}")

100%|██████████| 1214808/1214808 [00:01<00:00, 698081.34it/s]


square std of all: 9339.439088453108
Train: 7457.485829692388
Val: 14985.195529977862


/tmp/ipykernel_2270680/423166722.py:14: RuntimeWarning: divide by zero encountered in log
  df_raw["1h_volume"] = np.log(future_volume)


In [9]:
# ts = df_raw["timestamp"].values
# values = df_raw["value"].values
# df_size = len(df_raw)
# prefix_sum = np.zeros(df_size + 1)
# prefix_sum[1:] = np.cumsum(values)
# future_volume = np.zeros(df_size)
# j = 0
# for i in tqdm(range(df_size)):
#     while j < df_size and ts[j] <= ts[i] + 3600:
#         j += 1
#     future_volume[i] = prefix_sum[j] - prefix_sum[i + 1]
# df_raw["1h_volume"] = future_volume

In [10]:
import plotly.express as px

In [11]:
# px.line(
#     x=pd.to_datetime(df_raw["timestamp"][330000:420000], unit='s'),
#     y=df_raw["1h_volume"][330000:420000])

In [12]:
# df_raw = getattr(Dataloader, config['dataset_fabric'])(**{
#     **config['df_config'],
#     **{'end_block': 22000000},
# }, address_limit=config['cnt_known_address'])

In [13]:
# ts = df_raw["timestamp"].values
# values = df_raw["value"].values
# df_size = len(df_raw)

# prefix_sum = np.zeros(df_size + 1)
# prefix_sum[1:] = np.cumsum(values)

# future_volume = np.zeros(df_size)
# j = 0

# for i in tqdm(range(df_size)):
#     while j < df_size and ts[j] <= ts[i] + 3600:
#         j += 1
#     future_volume[i] = prefix_sum[j] - prefix_sum[i + 1]

# df_raw["1h_volume"] = future_volume

In [35]:
# px.line(np.log(train_data)[:1000])

In [39]:
train_df = TimeEmbeddingRegressionDataset(train_data, model, 100, apply_log=True, cnt_batchs=-1,
                                        target_type=target_type, device=device)

Embedding calculation:   0%|          | 0/72 [00:00<?, ?it/s]

/tmp/ipykernel_2270680/3558949823.py:114: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

Embedding calculation: 100%|██████████| 72/72 [00:30<00:00,  2.38it/s]

torch.Size([9110, 100, 4])


In [40]:

train_datalodader =  DataLoader(train_df, batch_size=batch_size, drop_last=True,
                                num_workers=12, persistent_workers=True, pin_memory=True)

val_df = TimeEmbeddingRegressionDataset(val_data, model, 100, apply_log=True, cnt_batchs=-1,
                                        target_type=target_type)
val_datalodader =  DataLoader(val_df, batch_size=batch_size, drop_last=True,
                            num_workers=12, persistent_workers=True, pin_memory=True)

wandb_logger = TargetLogger(target_type, run_name)


Embedding calculation:   0%|          | 0/24 [00:00<?, ?it/s]

/tmp/ipykernel_2270680/3558949823.py:114: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

Embedding calculation: 100%|██████████| 24/24 [00:12<00:00,  1.89it/s]

torch.Size([3036, 100, 4])


In [41]:
df_std=train_df[:][1].std()
df_mean=train_df[:][1].mean()

In [129]:
lr = 1e-3

In [130]:
study_epoch = 100

In [132]:
wandb_logger = TargetLogger(target_type, run_name)

time_model = SimpleRegressor(48)
try:
    train_time_regressor(time_model, train_datalodader, val_datalodader, num_epochs=study_epoch,
                        lr=lr, device=device, std=1, mean=0,
                        logger=wandb_logger, normilize=False)
except KeyboardInterrupt:
    pass

wandb_logger.finish()


/home/motatasher/miniconda3/envs/DiplomaIsupov/lib/python3.12/site-packages/torch/optim/lr_scheduler.py:62: UserWarning:

The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.

Epoch 1 - Train:   0%|          | 0/55 [00:00<?, ?it/s]/home/motatasher/miniconda3/envs/DiplomaIsupov/lib/python3.12/site-packages/torch/nn/modules/loss.py:610: UserWarning:

Using a target size (torch.Size([16384, 1, 1])) that is different to the input size (torch.Size([16384, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.

Epoch 1 - Val: 100%|██████████| 18/18 [00:00<00:00, 32.54it/s]


Epoch 1

Lr: 0.001

Train Loss: 8.5120

Val Loss: 3.1577

Timedelta: 0:00:03.157690


Epoch 2 - Val: 100%|██████████| 18/18 [00:00<00:00, 34.97it/s]


Epoch 2

Lr: 0.001

Train Loss: 2.1400

Val Loss: 1.7274

Timedelta: 0:00:01.727414


Epoch 3 - Val: 100%|██████████| 18/18 [00:00<00:00, 33.19it/s]


...

Epoch 98

Lr: 2.44140625e-07

Train Loss: 1.2864

Val Loss: 1.1855

Timedelta: 0:00:01.185512


Epoch 99 - Val: 100%|██████████| 18/18 [00:00<00:00, 35.40it/s]


Epoch 99

Lr: 2.44140625e-07

Train Loss: 1.2864

Val Loss: 1.1855

Timedelta: 0:00:01.185514


Epoch 100 - Val: 100%|██████████| 18/18 [00:00<00:00, 34.05it/s]

Epoch 100

Lr: 1.220703125e-07

Train Loss: 1.2864

Val Loss: 1.1855

Timedelta: 0:00:01.185516


In [133]:
df_std, df_mean

(tensor(1.2722), tensor(10.3300))

In [134]:
with torch.no_grad():
    res =  (time_model(train_df[:][0].to(device)) * 1 + 0).cpu().detach().numpy().reshape(-1)

In [135]:
N = 100
res_mean = (res.cumsum()[N:] - res.cumsum()[:-N]) / N

In [136]:
target = train_df[:][1].detach().cpu().numpy().reshape(-1)

In [137]:
res.mean(), res_mean.mean()

(np.float32(10.33363), np.float32(10.34402))

In [138]:
train_df[:][1].mean(), target.mean()

(tensor(10.3300), np.float32(10.330005))

In [139]:
for N in [1, 2, 3, 10, 30, 50, 100, 1000, 10000]:
    res_mean = (res.cumsum()[N:] - res.cumsum()[:-N]) / N
    print(np.corrcoef(np.array([np.diff(target[:-N]).reshape(-1), np.diff(res_mean).reshape(-1)]))[1, 0])

-0.000561006242754523
-0.0019379725876597267
-0.0004446233813779043
-0.0011576661153935637
-0.000984333981737794
-0.0008605579862009495
-0.0009571933026649988
-0.00038362002814907166
-0.00017402008079132599


In [140]:
N = 10
res_mean = (res.cumsum()[N:] - res.cumsum()[:-N]) / N

In [148]:
import plotly.graph_objects as go

fig = go.Figure()

start = 220
end = 300

start *= 1000
end *= 1000

# fig.add_trace(go.Line(y=res.reshape(-1)[start:end], name='predict', line_shape='hv'))
fig.add_trace(go.Line(y=res_mean.reshape(-1)[start:end], name='predict mean', line_shape='hv'))
fig.add_trace(go.Line(y=target.reshape(-1)[start:end], name='target', line_shape='hv'))

fig

In [85]:
go.Scatter(y=res.reshape(-1)[:10000])

Scatter({
    'y': array([46821.73 , 48630.188, 48628.75 , ..., 42722.758, 48557.707,
          48558.035], dtype=float32)
})

In [79]:
np.corrcoef(np.array([target, res]).reshape(2, -1))

array([[ 1.        , -0.00661803],
       [-0.00661803,  1.        ]])